In [ ]:
# -*- coding: utf-8 -*-

import matplotlib.pyplot as plt
import math
import pandas_datareader as web
import numpy as np
import pandas as pd
from sklearn.preprocessing import MinMaxScaler
from keras.models import Sequential
from keras.layers import Dense, LSTM
import yfinance as yf
import plotly.graph_objs as go

plt.style.use('fivethirtyeight')

def predict_stock_price(stock_symbol):
    # Télécharger les données pour la dernière année
    stock_data = yf.Ticker(stock_symbol).history(period="1y")

    # Prétraitement des données
    data = stock_data.filter(['Close'])
    dataset = data.values
    training_data_len = math.ceil(len(dataset) * 0.9)
    scaler = MinMaxScaler(feature_range=(0, 1))
    scaled_data = scaler.fit_transform(dataset)

    train_data = scaled_data[0:training_data_len, :]
    x_train = []
    y_train = []

    for i in range(60, len(train_data)):
        x_train.append(train_data[i-60:i, 0])
        y_train.append(train_data[i, 0])

    x_train, y_train = np.array(x_train), np.array(y_train)
    x_train = np.reshape(x_train, (x_train.shape[0], x_train.shape[1], 1))

    # Construction du modèle LSTM
    model = Sequential()
    model.add(LSTM(50, return_sequences=True, input_shape=(x_train.shape[1], 1)))
    model.add(LSTM(50, return_sequences=False))
    model.add(Dense(25))
    model.add(Dense(1))
    model.compile(optimizer='adam', loss='mean_squared_error')
    model.fit(x_train, y_train, batch_size=1, epochs=1)

    # Préparation des données de test
    test_data = scaled_data[training_data_len - 60:, :]
    x_test = []

    for i in range(60, len(test_data)):
        x_test.append(test_data[i-60:i, 0])

    x_test = np.array(x_test)
    x_test = np.reshape(x_test, (x_test.shape[0], x_test.shape[1], 1))

    # Prédictions sur les données de test
    predictions = model.predict(x_test)
    predictions = scaler.inverse_transform(predictions)

    # Visualisation des résultats
    train = data[:training_data_len]
    valid = data[training_data_len:]
    valid['Predictions'] = predictions

    # Visualisation avec Plotly
    trace_train = go.Scatter(x=train.index, y=train['Close'], mode='lines', name='Train')
    trace_valid = go.Scatter(x=valid.index, y=valid['Close'], mode='lines', name='Val')
    trace_predictions = go.Scatter(x=valid.index, y=valid['Predictions'], mode='lines', name='Predictions')

    fig = go.Figure()
    fig.add_trace(trace_train)
    fig.add_trace(trace_valid)
    fig.add_trace(trace_predictions)

    fig.update_layout(
        title=f'Modèle de prédiction pour {stock_symbol}',
        xaxis_title='Date',
        yaxis_title='Prix de clôture (USD)',
        legend=dict(x=0, y=1),
    )

    fig.show()

# Liste des symboles des actions à analyser
stocks_to_analyze = ['AAPL', 'BTC-USD', '^GSPC', 'JPM', 'GS', 'TSLA']

# Appliquer l'algorithme à chaque action
for stock_symbol in stocks_to_analyze:
    predict_stock_price(stock_symbol)


1/1 [==============================] - 1s 622ms/step


<ipython-input-3-35a6295c4224>:64: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



2/2 [==============================] - 1s 7ms/step


<ipython-input-3-35a6295c4224>:64: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



1/1 [==============================] - 1s 587ms/step


...

<ipython-input-3-35a6295c4224>:64: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



1/1 [==============================] - 1s 607ms/step


<ipython-input-3-35a6295c4224>:64: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



1/1 [==============================] - 1s 599ms/step


<ipython-input-3-35a6295c4224>:64: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [ ]:
# -*- coding: utf-8 -*-

import matplotlib.pyplot as plt
import math
import pandas_datareader as web
import numpy as np
import pandas as pd
from sklearn.preprocessing import MinMaxScaler
from keras.models import Sequential
from keras.layers import Dense, LSTM
import yfinance as yf
import plotly.graph_objs as go

plt.style.use('fivethirtyeight')

def evaluate_metrics(y_true, predictions):
    mse = mean_squared_error(y_true, predictions)
    mae = mean_absolute_error(y_true, predictions)
    r2 = r2_score(y_true, predictions)
    variance = explained_variance_score(y_true, predictions)
    max_err = max_error(y_true, predictions)

    return mse, mae, r2, variance, max_err

def predict_stock_price(stock_symbol):
    # Télécharger les données pour la dernière année
    stock_data = yf.Ticker(stock_symbol).history(period="1y")

    # Prétraitement des données
    data = stock_data.filter(['Close'])
    dataset = data.values
    training_data_len = math.ceil(len(dataset) * 0.9)
    scaler = MinMaxScaler(feature_range=(0, 1))
    scaled_data = scaler.fit_transform(dataset)

    train_data = scaled_data[0:training_data_len, :]
    x_train = []
    y_train = []

    for i in range(60, len(train_data)):
        x_train.append(train_data[i-60:i, 0])
        y_train.append(train_data[i, 0])

    x_train, y_train = np.array(x_train), np.array(y_train)
    x_train = np.reshape(x_train, (x_train.shape[0], x_train.shape[1], 1))

    # Construction du modèle LSTM
    model = Sequential()
    model.add(LSTM(50, return_sequences=True, input_shape=(x_train.shape[1], 1)))
    model.add(LSTM(50, return_sequences=False))
    model.add(Dense(25))
    model.add(Dense(1))
    model.compile(optimizer='adam', loss='mean_squared_error')
    model.fit(x_train, y_train, batch_size=1, epochs=1)

    # Préparation des données de test
    test_data = scaled_data[training_data_len - 60:, :]
    x_test = []
    y_test = dataset[training_data_len:, :]
    for i in range(60, len(test_data)):
        x_test.append(test_data[i-60 :i, 0])

    x_test = np.array(x_test)
    x_test = np.reshape(x_test, (x_test.shape[0], x_test.shape[1], 1))

    # Prédictions sur les données de test
    predictions = model.predict(x_test)
    predictions = scaler.inverse_transform(predictions)

    # Récupération des vraies valeurs pour les métriques
    y_test = y_test.flatten()

    # Évaluation des performances du modèle
    mse, mae, r2, variance, max_err = evaluate_metrics(y_test, predictions.flatten())

    print(f"Métriques d'évaluation pour {stock_symbol}:")
    print(f"MSE: {mse}")
    print(f"MAE: {mae}")
    print(f"R2 Score: {r2}")
    print(f"Variance: {variance}")
    print(f"Max Error: {max_err}")

    # Affichage des résultats
    train = data[:training_data_len]
    valid = data[training_data_len:]
    valid['Predictions'] = predictions
 # Visualisation avec Plotly
    trace_train = go.Scatter(x=train.index, y=train['Close'], mode='lines', name='Train')
    trace_valid = go.Scatter(x=valid.index, y=valid['Close'], mode='lines', name='Val')
    trace_predictions = go.Scatter(x=valid.index, y=valid['Predictions'], mode='lines', name='Predictions')

    fig = go.Figure()
    fig.add_trace(trace_train)
    fig.add_trace(trace_valid)
    fig.add_trace(trace_predictions)

    fig.update_layout(
        title=f'Modèle de prédiction pour {stock_symbol}',
        xaxis_title='Date',
        yaxis_title='Prix de clôture (USD)',
        legend=dict(x=0, y=1),
    )

    fig.show()


# Liste des symboles des actions à analyser
stocks_to_analyze = ['AAPL', 'BTC-USD', '^GSPC', 'JPM', 'GS', 'TSLA']

# Appliquer l'algorithme à chaque action
for stock_symbol in stocks_to_analyze:
    predict_stock_price(stock_symbol)



1/1 [==============================] - 1s 605ms/step
Métriques d'évaluation pour AAPL:
MSE: 21.226555979885163
MAE: 3.614166259765625
R2 Score: 0.24139966751570852
Variance: 0.2516880816563323
Max Error: 9.90240478515625


<ipython-input-9-fa9f45f14ff7>:86: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



2/2 [==============================] - 1s 8ms/step
Métriques d'évaluation pour BTC-USD:
MSE: 3057262.5213131374
MAE: 1501.8891059027778
R2 Score: -0.5625887494209068
Variance: 0.017102154570145967
Max Error: 3447.328125


<ipython-input-9-fa9f45f14ff7>:86: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



1/1 [==============================] - 1s 623ms/step
Métriques d'évaluation pour ^GSPC:
MSE: 10991.018402700423
MAE: 95.81908203125
R2 Score: -2.3511029602135936
Variance: 0.44822542682304023
Max Error: 164.1337890625


...

<ipython-input-9-fa9f45f14ff7>:86: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



1/1 [==============================] - 1s 597ms/step
Métriques d'évaluation pour GS:
MSE: 639.1853011746705
MAE: 24.252861328125
R2 Score: -2.983750287601744
Variance: 0.6822398789808705
Max Error: 43.661102294921875


<ipython-input-9-fa9f45f14ff7>:86: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



1/1 [==============================] - 1s 1s/step
Métriques d'évaluation pour TSLA:
MSE: 190.55788384383544
MAE: 10.809493408203124
R2 Score: -0.9316724725461114
Variance: -0.050265219297581876
Max Error: 31.965789794921875


<ipython-input-9-fa9f45f14ff7>:86: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [ ]:
import matplotlib.pyplot as plt
import math
import pandas_datareader as web
import numpy as np
import pandas as pd
from sklearn.preprocessing import MinMaxScaler
from keras.models import Sequential
from keras.layers import Dense, LSTM
import yfinance as yf
import plotly.graph_objs as go
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score, explained_variance_score, max_error
from IPython.display import display

plt.style.use('fivethirtyeight')

In [ ]:
def predict_stock_price(stock_data):
    # Prétraitement des données
    data = stock_data.filter(['Close'])
    dataset = data.values
    training_data_len = math.ceil(len(dataset) * 0.9)
    scaler = MinMaxScaler(feature_range=(0, 1))
    scaled_data = scaler.fit_transform(dataset)

    train_data = scaled_data[0:training_data_len, :]
    x_train = []
    y_train = []

    for i in range(60, len(train_data)):
        x_train.append(train_data[i-60:i, 0])
        y_train.append(train_data[i, 0])

    x_train, y_train = np.array(x_train), np.array(y_train)
    x_train = np.reshape(x_train, (x_train.shape[0], x_train.shape[1], 1))

    # Construction du modèle LSTM
    model = Sequential()
    model.add(LSTM(50, return_sequences=True, input_shape=(x_train.shape[1], 1)))
    model.add(LSTM(50, return_sequences=False))
    model.add(Dense(25))
    model.add(Dense(1))
    model.compile(optimizer='adam', loss='mean_squared_error')
    model.fit(x_train, y_train, batch_size=1, epochs=1)

    # Préparation des données de test
    test_data = scaled_data[training_data_len - 60:, :]
    x_test = []
    y_test = dataset[training_data_len:, :]
    for i in range(60, len(test_data)):
        x_test.append(test_data[i-60 :i, 0])

    x_test = np.array(x_test)
    x_test = np.reshape(x_test, (x_test.shape[0], x_test.shape[1], 1))

    # Prédictions sur les données de test
    predictions = model.predict(x_test)
    predictions = scaler.inverse_transform(predictions)

    return y_test.flatten(), predictions.flatten()


In [ ]:

def evaluate_metrics(y_true, predictions):
    mse = mean_squared_error(y_true, predictions)
    mae = mean_absolute_error(y_true, predictions)
    rmse = np.sqrt(mse)
    r2 = r2_score(y_true, predictions)
    variance = explained_variance_score(y_true, predictions)
    max_err = max_error(y_true, predictions)

    return mse, mae, rmse, r2, variance, max_err


In [ ]:

def visualize_results(stock_symbol, train, valid, predictions):
    trace_train = go.Scatter(x=train.index, y=train['Close'], mode='lines', name='Train')
    trace_valid = go.Scatter(x=valid.index, y=valid['Close'], mode='lines', name='Val')
    trace_predictions = go.Scatter(x=valid.index, y=valid['Predictions'], mode='lines', name='Predictions')

    fig = go.Figure()
    fig.add_trace(trace_train)
    fig.add_trace(trace_valid)
    fig.add_trace(trace_predictions)

    fig.update_layout(
        title=f'Modèle de prédiction pour {stock_symbol}',
        xaxis_title='Date',
        yaxis_title='Prix de clôture (USD)',
        legend=dict(x=0, y=1),
    )

    fig.show()


In [ ]:
def main():
    # Liste des symboles des actions à analyser
    stocks_to_analyze = ['AAPL', 'BTC-USD', '^GSPC', 'JPM', 'GS', 'TSLA','^IXIC']

    metrics_data = {'Stock': [], 'MSE': [], 'MAE': [], 'RMSE': [], 'R2 Score': [], 'Variance': [], 'Max Error': []}

    for stock_symbol in stocks_to_analyze:
        stock_data = yf.Ticker(stock_symbol).history(period="max")
        y_true, predictions = predict_stock_price(stock_data)
        mse, mae, rmse, r2, variance, max_err = evaluate_metrics(y_true, predictions)

        metrics_data['Stock'].append(stock_symbol)
        metrics_data['MSE'].append(mse)
        metrics_data['MAE'].append(mae)
        metrics_data['RMSE'].append(rmse)
        metrics_data['R2 Score'].append(r2)
        metrics_data['Variance'].append(variance)
        metrics_data['Max Error'].append(max_err)

        # Visualisation des résultats
        training_data_len = math.ceil(len(stock_data) * 0.9)
        train = stock_data[:training_data_len]
        valid = stock_data[training_data_len:]
        valid['Predictions'] = predictions
        visualize_results(stock_symbol, train, valid, predictions)

    # Création et affichage du DataFrame des métriques
    metrics_df = pd.DataFrame(metrics_data)
    print("Métriques pour chaque stock :")
    display(metrics_df)

if __name__ == "__main__":
    main()


34/34 [==============================] - 1s 5ms/step


<ipython-input-5-c714d5d9fe85>:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  valid['Predictions'] = predictions


11/11 [==============================] - 1s 5ms/step


<ipython-input-5-c714d5d9fe85>:24: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



76/76 [==============================] - 1s 5ms/step


...

<ipython-input-5-c714d5d9fe85>:24: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



11/11 [==============================] - 1s 5ms/step


<ipython-input-5-c714d5d9fe85>:24: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



Métriques pour chaque stock :


Stock           MSE          MAE         RMSE  R2 Score  Variance  \
0     AAPL  7.767533e+01     6.957440     8.813361  0.946157  0.975531   
1  BTC-USD  1.887458e+06  1022.600442  1373.847914  0.947905  0.967489   
2    ^GSPC  8.856765e+04   254.847295   297.603174  0.888332  0.970087   
3      JPM  1.908897e+01     3.652184     4.369093  0.963020  0.980765   
4       GS  6.831660e+01     6.622427     8.265386  0.920808  0.946667   
5     TSLA  1.506703e+02     9.682127    12.274782  0.923080  0.930461   

     Max Error  
0    21.670914  
1  5519.691406  
2   647.734131  
3    17.550697  
4    32.114227  
5    36.037262

In [ ]:
def main():
    # Liste des symboles des actions à analyser
    stocks_to_analyze = ['^IXIC']

    metrics_data = {'Stock': [], 'MSE': [], 'MAE': [], 'RMSE': [], 'R2 Score': [], 'Variance': [], 'Max Error': []}

    for stock_symbol in stocks_to_analyze:
        stock_data = yf.Ticker(stock_symbol).history(period="max")
        y_true, predictions = predict_stock_price(stock_data)
        mse, mae, rmse, r2, variance, max_err = evaluate_metrics(y_true, predictions)

        metrics_data['Stock'].append(stock_symbol)
        metrics_data['MSE'].append(mse)
        metrics_data['MAE'].append(mae)
        metrics_data['RMSE'].append(rmse)
        metrics_data['R2 Score'].append(r2)
        metrics_data['Variance'].append(variance)
        metrics_data['Max Error'].append(max_err)

        # Visualisation des résultats
        training_data_len = math.ceil(len(stock_data) * 0.9)
        train = stock_data[:training_data_len]
        valid = stock_data[training_data_len:]
        valid['Predictions'] = predictions
        visualize_results(stock_symbol, train, valid, predictions)

    # Création et affichage du DataFrame des métriques
    metrics_df = pd.DataFrame(metrics_data)
    print("Métriques pour chaque stock :")
    display(metrics_df)

if __name__ == "__main__":
    main()


42/42 [==============================] - 1s 4ms/step


<ipython-input-7-0b14fc21738d>:24: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



Métriques pour chaque stock :


Stock           MSE         MAE        RMSE  R2 Score  Variance  \
0  ^IXIC  82820.794322  230.212926  287.786022  0.988004  0.988421   

     Max Error  
0  1178.563477

In [ ]:
import yfinance as yf
from statsmodels.tsa.arima.model import ARIMA
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score

In [ ]:


def arima_predict(stock_data):
    to_row = int(len(stock_data) * 0.9)
    training_data = list(stock_data[0:to_row]['Adj Close'])
    testing_data = list(stock_data[to_row:]['Adj Close'])

    model_predictions = []
    n_test_obser = len(testing_data)

    for i in range(n_test_obser):
        # Utilisation de la classe ARIMA
        model = ARIMA(training_data, order=(4, 1, 0))
        model_fit = model.fit()

        # Prédiction d'une seule valeur
        yhat = model_fit.forecast(steps=1)[0]
        model_predictions.append(yhat)

        actual_test_value = testing_data[i]
        training_data.append(actual_test_value)

    return testing_data, model_predictions


In [ ]:
import plotly.graph_objs as go
from plotly.subplots import make_subplots
def plot_arima_results(stock_symbol, actual, predictions):
    fig = make_subplots(rows=1, cols=1, subplot_titles=[f'ARIMA Model - Prediction vs Actual for {stock_symbol}'])

    trace_actual = go.Scatter(x=list(range(len(actual))),
                             y=actual,
                             mode='lines',
                             name='Actual')

    trace_predicted = go.Scatter(x=list(range(len(actual), len(actual) + len(predictions))),
                                 y=predictions,
                                 mode='lines',
                                 name='Predicted')

    fig.add_trace(trace_actual)
    fig.add_trace(trace_predicted)

    fig.update_layout(xaxis_title='Time', yaxis_title='Adj Close Price', showlegend=True)
    fig.show()


In [ ]:

def calculate_metrics(actual, predictions):
    mse = mean_squared_error(actual, predictions)
    mae = mean_absolute_error(actual, predictions)
    r2 = r2_score(actual, predictions)

    return mse, mae, r2

# Utilisation des fonctions
stocks_to_analyze = ['AAPL', 'BTC-USD', '^GSPC', 'JPM', 'GS', 'TSLA', '^IXIC']

for stock_symbol in stocks_to_analyze:
    stock_data = yf.download(stock_symbol)
    actual_prices, arima_predictions = arima_predict(stock_data)

    # Visualisation des résultats
    plot_arima_results(stock_symbol, actual_prices, arima_predictions)

    # Calcul des métriques
    mse, mae, r2 = calculate_metrics(actual_prices, arima_predictions)

    # Affichage des métriques
    print(f"Métriques d'évaluation pour {stock_symbol}:")
    print(f"MSE: {mse}")
    print(f"MAE: {mae}")
    print(f"R2 Score: {r2}")
    print("\n")


[*********************100%%**********************]  1 of 1 completed


/usr/local/lib/python3.10/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

/usr/local/lib/python3.10/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

/usr/local/lib/python3.10/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

/usr/local/lib/python3.10/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

/usr/local/lib/python3.10/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

/usr/local/lib/python3.10/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning:

Maximum Likelihood optimization failed to converge. Check mle_retvals

/usr/local/lib/python3

Métriques d'évaluation pour AAPL:
MSE: 6.526798434516059
MAE: 1.868843053000708
R2 Score: 0.995490474138979


[*********************100%%**********************]  1 of 1 completed


Métriques d'évaluation pour BTC-USD:
MSE: 533367.4607774491
MAE: 476.357327746102
R2 Score: 0.9853041045192245


[*********************100%%**********************]  1 of 1 completed


KeyboardInterrupt: 

In [ ]:
import plotly.graph_objs as go
from plotly.subplots import make_subplots

def plot_arima_results(stock_symbol, actual, predictions):
    fig = make_subplots(rows=1, cols=1, subplot_titles=[f'ARIMA Model - Prediction vs Actual for {stock_symbol}'])

    trace_actual = go.Scatter(x=list(range(len(actual))),
                             y=actual,
                             mode='lines',
                             name='Actual')

    trace_predicted = go.Scatter(x=list(range(len(actual))),
                                 y=predictions,
                                 mode='lines',
                                 name='Predicted')

    fig.add_trace(trace_actual)
    fig.add_trace(trace_predicted)

    fig.update_layout(xaxis_title='Time', yaxis_title='Adj Close Price', showlegend=True)
    fig.show()


In [ ]:
stocks_to_analyze = ['AAPL']

for stock_symbol in stocks_to_analyze:
    stock_data = yf.download(stock_symbol)
    actual_prices, arima_predictions = arima_predict(stock_data)

plot_arima_results(stock_symbol, actual_prices, arima_predictions)

[*********************100%%**********************]  1 of 1 completed


/usr/local/lib/python3.10/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/usr/local/lib/python3.10/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/usr/local/lib/python3.10/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/usr/local/lib/python3.10/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
/usr/local/lib/python3.10/dist-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood op